In [19]:
#Required packages
import pandas as pd

from fastai.collab import *

In [20]:
orders_df = pd.read_csv("./Data/olist_orders_dataset.csv")
order_items_df = pd.read_csv("./Data/olist_order_items_dataset.csv")
#customer_df = pd.read_csv("./Data/olist_customers_dataset.csv")
reviews_df = pd.read_csv("./Data/olist_order_reviews_dataset.csv")
product_df = pd.read_csv("./Data/olist_products_dataset.csv")

In [21]:
orders_df[['order_id' , 'customer_id']]
order_items_df[['order_id','product_id']]
reviews_df[['order_id','review_score']]
product_df[['product_id','product_category_name']]

product_id              product_category_name
0      1e9e8ef04dbcff4541ed26657ea517e5                         perfumaria
1      3aa071139cb16b67ca9e5dea641aaa2f                              artes
2      96bd76ec8810374ed1b65e291975717f                      esporte_lazer
3      cef67bcfe19066a932b7673e239eb23d                              bebes
4      9dc1a7de274444849c219cff195d0b71              utilidades_domesticas
...                                 ...                                ...
32946  a0b7d5a992ccda646f2d34e418fff5a0                   moveis_decoracao
32947  bf4538d88321d0fd4412a93c974510e6  construcao_ferramentas_iluminacao
32948  9a7c6041fa9592d9d9ef6cfe62a71f8c                    cama_mesa_banho
32949  83808703fc0706a22e264b9d75f04a2e             informatica_acessorios
32950  106392145fca363410d287a815be6de4                    cama_mesa_banho

[32951 rows x 2 columns]

In [22]:
final_df = orders_df[['order_id', 'customer_id']].merge(order_items_df[['order_id', 'product_id']], on='order_id') \
                .merge(reviews_df[['order_id', 'review_score']], on='order_id') \
                .merge(product_df[['product_id', 'product_category_name']], left_on='product_id', right_on='product_id')
final_df.head()

order_id                       customer_id   
0  e481f51cbdc54678b7cc49136f2d6af7  9ef432eb6251297304e76186b10a928d  \
1  128e10d95713541c87cd1a2e48201934  a20e8105f23924cd00833fd87daa0831   
2  0e7e841ddf8f8f2de2bad69267ecfbcf  26c7ac168e1433912a51b924fbd34d34   
3  bfc39df4f36c3693ff3b63fcbea9e90a  53904ddbea91e1e92b2b3f1d09a7af86   
4  53cdb2fc8bc7dce0b6741e2150273451  b0830fb4747a6c6d20dea0b8c802d7ef   

                         product_id  review_score  product_category_name  
0  87285b34884572647811a353c7ac498a             4  utilidades_domesticas  
1  87285b34884572647811a353c7ac498a             4  utilidades_domesticas  
2  87285b34884572647811a353c7ac498a             5  utilidades_domesticas  
3  87285b34884572647811a353c7ac498a             3  utilidades_domesticas  
4  595fac2a385ac33a80bd5114aec74eb8             4             perfumaria

In [23]:
# Create a user and item index mapping
user_index = final_df['customer_id'].astype('category').cat.codes.values
item_index = final_df['product_id'].astype('category').cat.codes.values

# Create a DataLoaders object
dls = CollabDataLoaders.from_df(final_df, user_name='customer_id', item_name='product_id', rating_name='review_score', bs=64)

In [24]:
learn = collab_learner(dls, n_factors=100, y_range=(0, 5.5))
# Train the model
learn.fit_one_cycle(5, 5e-3, wd=0.1)

In [26]:
# # Matrix Factorization
# learn = collab_learner(dls, use_nn=False, y_range=(0, 5.5))
# learn.fit_one_cycle(10, 1e-2, wd=0.1)

# # Neural Collaborative Filtering
# learn = collab_learner(dls, use_nn=True, y_range=(0, 5.5))
# learn.fit_one_cycle(10, 1e-2, wd=0.1)


#model_path = './Data/'
learn.export()

In [35]:
from fastai.tabular.data import TabularPandas, TabDataLoader

# Assuming you have a DataFrame named 'new_data' containing 'customer_id' and 'product_id'
new_data = pd.DataFrame({
    'customer_id': [target_user] * len(learn.dls.classes['product_id']),
    'product_id': [learn.dls.classes['product_id'][i] for i in item_indices]
})

# Create a TabularPandas object for batch inference
test_dl = learn.dls.test_dl(new_data)

# Get predictions from the model using the DataLoader
preds = learn.get_preds(dl=test_dl, with_input=False, with_decoded=False)

# Extract predictions from the tuple
pred_scores = preds[0]

# Sort the recommendations by descending predicted score
recommended_indices = pred_scores.argsort(descending=True)[:5].tolist()  # Convert tensor to list

# Get recommended product IDs and their corresponding categories
recommended_products = [learn.dls.classes['product_id'][i] for i in recommended_indices]
recommended_categories = [final_df.loc[final_df['product_id'] == prod_id, 'product_category_name'].iloc[0] for prod_id in recommended_products]

# Print recommended products and their categories
for prod, cat in zip(recommended_products, recommended_categories):
    print(f"Recommended product: {prod} (Category: {cat})")


Recommended product: 54d9ac713e253fa1fae9c8003b011c2a (Category: cool_stuff)
Recommended product: d6160fb7873f184099d9bc95e30376af (Category: pcs)
Recommended product: ec2d43cc59763ec91694573b31f1c29a (Category: cama_mesa_banho)
Recommended product: 368c6c730842d78016ad823897a372db (Category: ferramentas_jardim)
Recommended product: 98d61056e0568ba048e5d78038790e77 (Category: automotivo)


In [36]:
# Replace 'target_user' with the actual customer_id for whom you want recommendations
target_user = '26c7ac168e1433912a51b924fbd34d34'
item_indices = range(len(learn.dls.classes['product_id']))

# Create a DataFrame with customer_id and product_id for batch inference
batch_data = pd.DataFrame({
    'customer_id': [target_user] * len(item_indices),
    'product_id': [learn.dls.classes['product_id'][i] for i in item_indices]
})

# Create a DataLoader for batch inference
batch_dl = learn.dls.test_dl(batch_data)

# Get predictions from the model using the DataLoader
preds = learn.get_preds(dl=batch_dl, with_input=False, with_decoded=False)[0]

# Sort the recommendations by descending predicted score
recommended_indices = preds.argsort(descending=True)[:15].tolist()  # You can adjust the number of recommendations

# Get recommended product IDs and their corresponding categories
recommended_products = [learn.dls.classes['product_id'][i] for i in recommended_indices]
recommended_categories = [final_df.loc[final_df['product_id'] == prod_id, 'product_category_name'].iloc[0] for prod_id in recommended_products]

# Print recommended products and their categories
for rank, (prod, cat) in enumerate(zip(recommended_products, recommended_categories), start=1):
    print(f"Rank {rank}: Recommended product: {prod} (Category: {cat})")


Rank 1: Recommended product: 54d9ac713e253fa1fae9c8003b011c2a (Category: cool_stuff)
Rank 2: Recommended product: ec2d43cc59763ec91694573b31f1c29a (Category: cama_mesa_banho)
Rank 3: Recommended product: d6160fb7873f184099d9bc95e30376af (Category: pcs)
Rank 4: Recommended product: 368c6c730842d78016ad823897a372db (Category: ferramentas_jardim)
Rank 5: Recommended product: 98d61056e0568ba048e5d78038790e77 (Category: automotivo)
Rank 6: Recommended product: f731f8587d4088c174397e010cf892a9 (Category: perfumaria)
Rank 7: Recommended product: bb90206fa281c20f0b4c42a2393b54dd (Category: informatica_acessorios)
Rank 8: Recommended product: 84f456958365164420cfc80fbe4c7fab (Category: cama_mesa_banho)
Rank 9: Recommended product: 24c66f106f642621e524291a895c9032 (Category: beleza_saude)
Rank 10: Recommended product: 78119fbfa709d07b86f5ccf15043c6d6 (Category: cool_stuff)
Rank 11: Recommended product: cd48f265a63e13b762601f5f794c5fca (Category: bebidas)
Rank 12: Recommended product: e9a69340883

In [38]:
from elasticsearch import Elasticsearch

# Initialize Elasticsearch client
es = Elasticsearch([{'host': 'localhost', 'port': 9200, 'scheme': 'http'}])  # Replace with your Elasticsearch host and port

# Iterate through all customer IDs
for target_user in final_df['customer_id'].unique():
    # Generate recommendations for the current customer
    # ... (your recommendation code here)

    # Prepare the recommendations data
    recommendations = []
    for rank, (prod, cat) in enumerate(zip(recommended_products, recommended_categories), start=1):
        recommendations.append({
            'product_id': prod,
            'product_name': 'Product Name',  # Replace with actual product name
            'category': cat
        })

    # Index the recommendations in Elasticsearch
    es.index(index='customer_recommendations', id=target_user, body={'recommendations': recommendations})

    print(f"Recommendations for customer {target_user} have been indexed in Elasticsearch.")


C:\Users\chand\AppData\Local\Temp\ipykernel_2124\1603449954.py:21: DeprecationWarning: The 'body' parameter is deprecated and will be removed in a future version. Instead use the 'document' parameter. See https://github.com/elastic/elasticsearch-py/issues/1698 for more information
  es.index(index='customer_recommendations', id=target_user, body={'recommendations': recommendations})
C:\Users\chand\AppData\Local\Temp\ipykernel_2124\1603449954.py:21: ElasticsearchWarning: Elasticsearch built-in security features are not enabled. Without authentication, your cluster could be accessible to anyone. See https://www.elastic.co/guide/en/elasticsearch/reference/7.17/security-minimal-setup.html to enable security.
  es.index(index='customer_recommendations', id=target_user, body={'recommendations': recommendations})


Recommendations for customer 9ef432eb6251297304e76186b10a928d have been indexed in Elasticsearch.
Recommendations for customer a20e8105f23924cd00833fd87daa0831 have been indexed in Elasticsearch.
Recommendations for customer 26c7ac168e1433912a51b924fbd34d34 have been indexed in Elasticsearch.
Recommendations for customer 53904ddbea91e1e92b2b3f1d09a7af86 have been indexed in Elasticsearch.
Recommendations for customer b0830fb4747a6c6d20dea0b8c802d7ef have been indexed in Elasticsearch.
Recommendations for customer 67407057a7d5ee17d1cd09523f484d13 have been indexed in Elasticsearch.
Recommendations for customer 1b338293f35549b5e480b9a3d7bbf3cd have been indexed in Elasticsearch.
Recommendations for customer e1365d7b227b247b6bc0931771885eaf have been indexed in Elasticsearch.
Recommendations for customer 7f4f07b97783e894fccff9d72e0988b3 have been indexed in Elasticsearch.
Recommendations for customer ff83b1b9ffb0f2f60273867bb26f671e have been indexed in Elasticsearch.
Recommendations for 

: 

: 